In [18]:
%load_ext autoreload
%autoreload 2

import json
from run_optimisations import run_optimisation
import plotly.graph_objects as go

import torch
from tqdm import tqdm
import sys
sys.path.insert(1, "external/MeshSDF")
from lib.models.decoder import DeepSDF

from src.sdf_convertion import reconstruct_trimesh
from src import tools

DEVICE = "cuda:2"

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Optimisation

In [3]:
sum = run_optimisation("optimisation_runs/test.json", num_iters = 3)

# Visualize 

In [24]:
with open("optimisation_runs/v1.json", "r") as f:
    summary = json.load(f)

fig = go.Figure(data=[go.Scatter(y=summary["run"]["metrics"])])
fig.update_layout(template="plotly_dark")
fig.show()

In [25]:
# Load the model
experiment_dir = "runs/wolfish_e256/"

specs = json.load(open(os.path.join(experiment_dir, "specs.json")))
train_mapping = json.load(open(specs["TrainSplit"]))
data_mapping = json.load(open("/".join(specs["TrainSplit"].split("/")[:-1] + ["mapping.json"])))

# Load the model
decoder = torch.nn.DataParallel(DeepSDF(specs["CodeLength"],  **specs["NetworkSpecs"]), device_ids=[DEVICE])
saved_model_state = torch.load(
    os.path.join(experiment_dir, "ModelParameters", "latest.pth"), map_location=DEVICE
)
decoder.load_state_dict(saved_model_state["model_state_dict"])
decoder = decoder.eval()

# Load latent codes
orig_latents = torch.load(os.path.join(experiment_dir, "LatentCodes/latest.pth"), map_location=DEVICE)["latent_codes"]["weight"]

shapes_reconstructed = []
for code in tqdm(summary["run"]["latents"][::2]):
    latent = torch.tensor(code).to(DEVICE)
    voxels = reconstruct_trimesh(decoder, latent, N=[128, 64, 64])
    shapes_reconstructed.append(voxels)

100%|██████████| 3/3 [00:01<00:00,  1.61it/s]


In [27]:
traces = []
for verts, faces in shapes_reconstructed:
    traces.append(tools.plot_3d_mesh(verts, faces))
tools.show_grid(*traces)
tools.show_grid([tr[0] for tr in traces])